Convert replay links from showdown website to json files that we can parse from.

In [ ]:
import requests
import json
import os

def read_replay_links(file_path):
    with open(file_path, "r") as f:
        return [line.strip() for line in f.readlines() if line.strip()]

def download_replay_data(urls, output_dir="12-11-replays"):

    os.makedirs(output_dir, exist_ok=True)

    for url in urls:
        replay_id = url.split("/")[-1]
        json_url = f"{url}.json"
        try:
            response = requests.get(json_url)
            if response.status_code == 200:
                data = response.json()
                with open(os.path.join(output_dir, f"{replay_id}.json"), "w") as f:
                    json.dump(data, f)
                print(f"Saved replay: {replay_id}")
            else:
                print(f"Failed to download {url}")
        except Exception as e:
            print(f"Error downloading {url}: {e}")

def main():
    #change inpout file for future inputss and stuff
    input_file = "replay_links/12-11_replays.txt"
    replay_urls = read_replay_links(input_file)
    download_replay_data(replay_urls)

if __name__ == "__main__":
    main()

Saved replay: gen9randombattle-2256914054
Saved replay: gen9randombattle-2254530768
Saved replay: gen9randombattle-2252095054
Saved replay: gen9randombattle-2240861265
Saved replay: gen9randombattle-2230351299
Saved replay: gen9randombattle-2221009399
Saved replay: gen9randombattle-2217274962
Saved replay: gen9randombattle-2212681226
Saved replay: gen9randombattle-2202575078
Saved replay: gen9randombattle-2202553193
Saved replay: gen9randombattle-2202548436
Saved replay: gen9randombattle-2202543991
Saved replay: gen9randombattle-2202537933
Saved replay: gen9randombattle-2202533468
Saved replay: gen9randombattle-2202484090
Saved replay: gen9randombattle-2202453938
Saved replay: gen9randombattle-2202180689
Saved replay: gen9randombattle-2202149438
Saved replay: gen9randombattle-2197139572
Saved replay: gen9randombattle-2192220691
Saved replay: gen9randombattle-2187585455
Saved replay: gen9randombattle-2174873559
Saved replay: gen9randombattle-2174303998
Saved replay: gen9randombattle-217

Parse the data in the json fiules so that it can actually be used for ml

In [2]:
#consider addding available moves but i dont think the replay file has that info, would have to search through it manually and add the moves each pokemon usese in the battle
#consider abilities, guts makes burn good and not bad
#consider stats of the pokemon, can be calculated if we need them
#consider so mnuch shit, but we start with this data and see how well we can get it to perform
#i feel like ratings should be considered added but idk where=
# {
#   "turn": 15,
#   "player": {
#     "active_pokemon": {
#       "species": "Charizard",
#       "hp_percent": 65,
#       "status": null,
#       "boosts": {"attack": 1, "defense": 0, "speed": -1}
#     },
#     "remainiing_pokemon": ["Blastoise", "Venusaur"]
#     "num_remaining_pokemon": 6
#   },
#   "opponent": {
#     "active_pokemon": {
#       "species": "Tyranitar",
#       "hp_percent": 30,
#       "status": "burned",
#       "
# 
# s": {"attack": -2, "defense": 0, "speed": 1}
#     },
#     "remaining_pokemon": 6
#     "Seen pokemon" : ['Pikachu']
#     "rating: " 1500
#   },
#   "battle_state": {
#     "weather": "sandstorm",
#     "terrain": null,
#     "entry_hazards": {"stealth_rock": true, "spikes": 2},
#     "trick_room": false,
#     "tailwind": false
#   },
#   "outcome": 0.7  // Example win rate for training data
# }

def create_game_state():
    game_state_data = {
        "turn": 0,
        "player": {
            #conside adding move and abilities of the mon, but iodk if thats needed
            "active_pokemon": {
                #500
                "mon": None,
                "hp_percent": 1.00000,
                # statuses = ["None", "Burn", "Poison", "Paralysis", "Sleep", "Freeze"] hot one
                "status": [1, 0, 0, 0, 0, 0],
                # hot one all 0s = none
                "terratype": [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0],

                
            },
            "boosts": {
                "atk": 0,       # -1 to 1  normalized from -6,6
                "def": 0,     
                "spa": 0,   
                "spd": 0,   
                "spe": 0,   
                'evasion' : 0,    
                "accuracy": 0      
            },
            "player_side_effects" : {
                "Stealth": 0,  #layers?  #stealth rock # im sad right now so i will settle
                "Spikes": 0,        
                "Toxic": 0,  #toxic spikers
                "Sticky": 0,    #sticky web
                "Reflect": 0,
                "reflect_turns": 0,
                "tailwind": 0,
                "tailwind_turns": 0 
            },
            "last_move": None,# probs some embedding later
            "next_move": None,# probs some embedding later
            "num_mons_left": None,
            "seen_pokemon": {
                "poke1": {"mon": "dontknow", "hp_percent": 1.0, "status": [1, 0, 0, 0, 0, 0], "terratype": [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]},
                "poke2": {"mon": "dontknow", "hp_percent": 1.0, "status": [1, 0, 0, 0, 0, 0], "terratype": [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]},
                "poke3": {"mon": "dontknow", "hp_percent": 1.0, "status": [1, 0, 0, 0, 0, 0], "terratype": [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]},
                "poke4": {"mon": "dontknow", "hp_percent": 1.0, "status": [1, 0, 0, 0, 0, 0], "terratype": [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]},
                "poke5": {"mon": "dontknow", "hp_percent": 1.0, "status": [1, 0, 0, 0, 0, 0], "terratype": [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]},
                "poke6": {"mon": "dontknow", "hp_percent": 1.0, "status": [1, 0, 0, 0, 0, 0], "terratype": [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]},
            },
            "terra_used": 0
        },
        "opponent": {
            "active_pokemon": {
                "mon": None,
                "hp_percent": 1.00000 ,
                "status": [1, 0, 0, 0, 0, 0],
                "terratype": [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
            },
            "boosts": {
                "atk": 0,      #-1,1
                "def": 0,     
                "spa": 0,   
                "spd": 0,   
                "spe": 0,   
                'evasion' : 0,    
                "accuracy": 0      
            },
            "opponent_side_effects" : {
                "stealth_rock": 0,  
                "spikes": 0,        
                "toxic_spikes": 0,  
                "sticky_web": 0 ,  
                "Reflect": 0,
                "reflect_turns": 0,
                "tailwind": 0,
                "tailwind_turns": 0
            },
            "last_move": None,# probs some embedding later
            "num_mons_left": None,
            "next_move": None, # probs some embedding later
            "seen_pokemon": {
                "poke1": {"mon": "dontknow", "hp_percent": 1.0, "status": [1, 0, 0, 0, 0, 0], "terratype": [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]},
                "poke2": {"mon": "dontknow", "hp_percent": 1.0, "status": [1, 0, 0, 0, 0, 0], "terratype": [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]},
                "poke3": {"mon": "dontknow", "hp_percent": 1.0, "status": [1, 0, 0, 0, 0, 0], "terratype": [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]},
                "poke4": {"mon": "dontknow", "hp_percent": 1.0, "status": [1, 0, 0, 0, 0, 0], "terratype": [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]},
                "poke5": {"mon": "dontknow", "hp_percent": 1.0, "status": [1, 0, 0, 0, 0, 0], "terratype": [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]},
                "poke6": {"mon": "dontknow", "hp_percent": 1.0, "status": [1, 0, 0, 0, 0, 0], "terratype": [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]},
            },
            "terra_used": 0 # 0 no, 1 yes
        },
        "battle_state": {
            #[NoWeather, SunnyDay, RainDance, Snow, SandStorm ]
            "weather": [1,0,0,0,0],
            'weather_turns_left': 0,
            #[NoTerrain, mistyterrain, grassyterrain, electricterrain, psychicterrain]
            "terrain": [1,0,0,0,0],
            'terrain_turns_left' : 0,
            "trick_room": 0, # 0 no, 1 yes
            "trick_room_turns": 0
        },
        "est_winrate": 0.5
    }
    return game_state_data

Hot one some stufff

In [3]:
import numpy as np

weather_events = ['none', 'SunnyDay', 'RainDance', 'Snow', 'Sandstorm' ]

weather_to_index = {weather: idx for idx, weather in enumerate(weather_events)}

def one_hot_encode_weather(current_weather):

    one_hot = np.zeros(len(weather_events))
    if current_weather in weather_to_index:

        one_hot[weather_to_index[current_weather]] = 1
    else:
        raise ValueError(f"Unhandled weather event: {current_weather}")
    return one_hot.tolist()

terrain_events = ['NoTerrain', 'Misty', 'Grassy', 'Electric', 'Psychic']

terrain_to_index = {terrain: idx for idx, terrain in enumerate(terrain_events)}

def one_hot_encode_terrain(current_terrain):

    one_hot = np.zeros(len(terrain_events))
    if current_terrain in terrain_to_index:

        one_hot[terrain_to_index[current_terrain]] = 1
    else:
        raise ValueError(f"Unhandled terrain event: {current_terrain}")
    return one_hot.tolist()


status_events =  ["None", "brn", "psn", "par", "slp", "frz", "tox"]

status_to_index = {terrain: idx for idx, terrain in enumerate(status_events)}


def hot_one_status(status):
    one_hot = np.zeros(len(status_events))
    if status in status_to_index:

        one_hot[status_to_index[status]] = 1
    else:
        raise ValueError(f"Unhandled status event: {status}")
    return one_hot.tolist()
    
types = [
    "Normal", "Fire", "Water", "Electric", "Grass", "Ice", "Fighting",
    "Poison", "Ground", "Flying", "Psychic", "Bug", "Rock", "Ghost",
    "Dragon", "Dark", "Steel", "Fairy"
]
type_to_index = {type_name: i for i, type_name in enumerate(types)}

def hot_terratype(terratype, type_to_index):
    # Initialize an all-zero array
    one_hot = np.zeros(len(types), dtype=int)
    
    # If terratype is None, return all zeros
    if terratype is None:
        return one_hot
    
    # Set the corresponding index to 1
    if terratype in type_to_index:
        one_hot[type_to_index[terratype]] = 1
    return one_hot.tolist()

Embedding pokemon

In [4]:
# from tensorflow.keras.layers import Embedding, Input, Concatenate
# from tensorflow.keras.models import Model



In [6]:

import os
import json
import re
import random
import math
import copy
#Gets the username and the rating given the correct string
def extract_username_and_rating(string):

    pattern = r"^(.+?)'s rating: (\d+)"
    match = re.search(pattern, string)
    if match:
        username = match.group(1)  
        rating = int(match.group(2)) 
        return username, rating
    else:
        return None, None

# return a smoothed winrate that increases/decreases depending on the out come
def smooth_win_rates(win, total_turns, curr_turn):

    progress = int(curr_turn) / int(total_turns)
    # Sigmoid so, more uncertain at the beginning but more sure at the end
    adjustment = 1 / (1 + math.exp(-10 * (progress - 0.5)))  
    estimated_win_rate = 0.5 + adjustment * 0.5 if win else 0.5 - adjustment * 0.5
    return estimated_win_rate

def extract_p1_pokemon(log):
    p1_pokemon = set()


    switch_pattern = re.compile(r"switch\|p1[a-d]?: ([A-Za-z0-9' -]+)\|([A-Za-z0-9' -]+)")  # Captures full name and form

    log_lines = log.splitlines()
    for line in log_lines:
        switch_match = switch_pattern.search(line)
        if switch_match:

            specific_pokemon_name = switch_match.group(2).strip()
            p1_pokemon.add(specific_pokemon_name)

    return p1_pokemon
#gets the winner of the game and the opponent's rating
def get_opp_rating(log, opponent):
    lines = log.splitlines()
    ret_rating = None
    winner = None
    for line in reversed(lines):

        parts = line.split('|')
        if len(parts) >= 2:
            if parts[1] == 'raw':
                name, rating  = extract_username_and_rating(parts[2])

                if name == opponent:

                    ret_rating = int(rating)
                    
            elif parts[1] == 'win':
                winner = parts[2]
                
            elif parts[1] == 'turn':
                total_turns = parts[2]
                return ret_rating, winner, total_turns
            
    return winner,ret_rating,total_turns
def record_switch(parts):
    # Update active Pokémon and their HP
    actor = parts[2]
    pokemon_info = parts[3].split(", ")
    new_pokemon = pokemon_info[0]
    new_hp = parts[4].split("/")  # Extract current HP
    new_hp = round(int(new_hp[0])/int(new_hp[1].split(' ')[0]), 5)
    return new_pokemon, new_hp

def get_pokemon_index(pokemon1,poke_to_index):
    pokemon = pokemon1.split('-')[0]
    if pokemon not in poke_to_index:
        i = len(poke_to_index) + 1
        poke_to_index[pokemon] = f"poke{i}"
    return poke_to_index[pokemon], poke_to_index


def name_from_line(line):

    pattern = re.compile(r"p[12][a-d]?: ([A-Za-z0-9' -]+)")
    
    match = pattern.search(line)
    if match:
        return match.group(1).strip()
    return None


#no we dont need start cause we should never be trying to calculatng the wr for the start yhou silly nugget
def parse_data(log, winner, op_rating, player, total_turns, probability = 0.3, player_pokemon = []):

    opponent_remaining = 6 
    player_remaining_mons = 6  
    game_states = []
    start = False
    record_turn = False
    p1_last_move = None
    op_last_move = None
    record_move_after = False
    player_pokemon_to_index = {}
    opponent_pokemon_to_index = {}
    win = 1 if winner == player else 0
    start_count = 0
    game_state = create_game_state()
    game_state['opponent']['rating'] = op_rating
    for pokemon in player_pokemon:
        idx, player_pokemon_to_index = get_pokemon_index(pokemon,player_pokemon_to_index)
        game_state["player"]['seen_pokemon'][idx]["mon"] = pokemon
        

    lines = log.splitlines()
    for line in lines:
        #note line_as_arr[0] will always be '' since every line starts with a |
        parts = line.split('|')
        
       
        if len(parts) >= 2:
            event = parts[1]
            # Save the game state at the end of the turn
            if record_move_after and event == "turn":

                last_game_state = game_states[-1]  # Get the last game state

                # Update the next move for player and opponent based on the current parsed turn
                last_game_state["player"]["next_move"] = p1_last_move
                last_game_state["opponent"]["next_move"] = op_last_move

                game_states[-1] = last_game_state
                record_move_after = False
                pass
            if record_turn and event == "turn":
                record_turn = False
                # game_state["opponent"]["seen_pokemon"] = opponent_seen
                game_state["opponent"]["num_mons_left"] = opponent_remaining
                # game_state["player"]["seen_pokemon"] = player_seen
                game_state["player"]["num_mons_left"] = player_remaining_mons
                game_states.append(copy.deepcopy(game_state))
                record_move_after = True
            
            if event == "turn" and not record_turn:
                
                if game_state['battle_state']['weather_turns_left'] != 0:
                    game_state['battle_state']['weather_turns_left']  -= 1
                else:
                    game_state['battle_state']['weather'] = one_hot_encode_weather('none')
                    
                if game_state['battle_state']['terrain_turns_left'] != 0:
                    game_state['battle_state']['terrain_turns_left']  -= 1
                else:
                    game_state['battle_state']['terrain'] = one_hot_encode_terrain('NoTerrain')

                if game_state['battle_state']['trick_room_turns'] != 0:
                    game_state['battle_state']['trick_room_turns']  -= 1
                else:
                    game_state['battle_state']['trick_room'] = 0

                if game_state['opponent']["opponent_side_effects"]['reflect_turns'] != 0:
                    game_state['opponent']["opponent_side_effects"]['reflect_turns'] -= 1
                    
                else:
                    game_state['opponent']["opponent_side_effects"]['Reflect'] = 0

                if game_state['player']["player_side_effects"]['reflect_turns'] != 0:
                    game_state['player']["player_side_effects"]['reflect_turns'] -= 1
                    
                else:
                    game_state['player']["player_side_effects"]['Reflect'] = 0
                
                game_state['turn'] = parts[2]
                pcurr_mon = game_state["player"]["active_pokemon"]["mon"]
                index, player_pokemon_to_index = get_pokemon_index(pcurr_mon, player_pokemon_to_index)

                game_state["player"]['seen_pokemon'][index]['hp_percent'] = game_state["player"]["active_pokemon"]["hp_percent"]
                game_state["player"]['seen_pokemon'][index]['status'] = game_state["player"]['active_pokemon']['status']
                game_state["player"]['seen_pokemon'][index]['terratype'] = game_state["player"]['active_pokemon']['terratype']
                ocurr_mon = game_state["opponent"]["active_pokemon"]["mon"]
                index,  opponent_pokemon_to_index = get_pokemon_index(ocurr_mon, opponent_pokemon_to_index)

                game_state["opponent"]['seen_pokemon'][index]['hp_percent'] = game_state["opponent"]["active_pokemon"]["hp_percent"]
                game_state["opponent"]['seen_pokemon'][index]['status'] = game_state["opponent"]['active_pokemon']['status']
                game_state["opponent"]['seen_pokemon'][index]['terratype'] = game_state["opponent"]['active_pokemon']['terratype']

                game_state['est_winrate'] = smooth_win_rates(win, total_turns, game_state['turn'])
                if random.random() < probability:
                    
                    record_turn = True
                    

            elif event == "start":
                start = True
            if start:
                
                if event == 'switch':
                    actor = parts[2]
                    new_pokemon, new_hp = record_switch(parts)
  
                    if actor.startswith('p2a'):
                        game_state["opponent"]["active_pokemon"]["mon"] = new_pokemon
                        game_state["opponent"]["active_pokemon"]["hp_percent"] = new_hp

                        index, opponent_pokemon_to_index = get_pokemon_index(new_pokemon, opponent_pokemon_to_index)
                        game_state["opponent"]['seen_pokemon'][index]['mon'] = new_pokemon
                        game_state["opponent"]['seen_pokemon'][index]['mon'] = new_hp


                    else:

                        game_state["player"]["active_pokemon"]["mon"] = new_pokemon
                        game_state["player"]["active_pokemon"]["hp_percent"] = new_hp

                    start_count += 1
                    if start_count == 2:
                        start = False
                
            if event == "move":
                # Log the last move for player or opponent
                actor = parts[2]
                move_name = parts[3]

                if actor.startswith("p1a"):
                    game_state["player"]["last_move"] = move_name
                    p1_last_move = move_name


                elif actor.startswith("p2a"):
                    game_state["opponent"]["last_move"] = move_name
                    op_last_move = move_name
                

            elif event == "switch":
                # Update active Pokémon and their
                actor = parts[2]

                new_pokemon, new_hp = record_switch(parts)
                if actor.startswith("p1a"):
                    prev_mon = game_state["player"]["active_pokemon"]["mon"]
                    index, player_pokemon_to_index = get_pokemon_index(prev_mon, player_pokemon_to_index)
                    print(player_pokemon_to_index )
                    game_state["player"]['seen_pokemon'][index]['hp_percent'] = game_state["player"]["active_pokemon"]["hp_percent"]
                    game_state["player"]['seen_pokemon'][index]['status'] = game_state["player"]['active_pokemon']['status']
                    game_state["player"]['seen_pokemon'][index]['terratype'] = game_state["player"]['active_pokemon']['terratype']

                    game_state["player"]["active_pokemon"]["mon"] = new_pokemon
                    game_state["player"]["active_pokemon"]["hp_percent"] = new_hp
                    
                elif actor.startswith("p2a"):
                    ocurr_mon = game_state["opponent"]["active_pokemon"]["mon"]
                    index, opponent_pokemon_to_index = get_pokemon_index(ocurr_mon, opponent_pokemon_to_index)
                    print(opponent_pokemon_to_index)
                    game_state["opponent"]['seen_pokemon'][index]['hp_percent'] = game_state["opponent"]["active_pokemon"]["hp_percent"]
                    game_state["opponent"]['seen_pokemon'][index]['status'] = game_state["opponent"]['active_pokemon']['status']
                    game_state["opponent"]['seen_pokemon'][index]['terratype'] = game_state["opponent"]['active_pokemon']['terratype']

                    game_state["opponent"]["active_pokemon"]["mon"] = new_pokemon
                    game_state["opponent"]["active_pokemon"]["hp_percent"] = new_hp
    

            elif event == "-damage":
                # Update HP of the affected Pokémon
                target = parts[2]
                new_hp = parts[3].split("/")  # Extract current HP
                if len(new_hp) == 1:
                    new_hp = 0
                else:
                    new_hp = round(int(new_hp[0])/int(new_hp[1].split(' ')[0]), 5)

                if target.startswith("p1a"):
                    game_state["player"]["active_pokemon"]["hp_percent"] = new_hp
                    
                elif target.startswith("p2a"):
                    game_state["opponent"]["active_pokemon"]["hp_percent"] = new_hp
                    
            elif event == 'faint':
                #pokemon marked with name dead, embbeded later
                info = parts[2].split(' ')
                target = info[0]
                fainted = name_from_line(parts[2])
                
                
                if target.startswith("p1a"):
                    index, player_pokemon_to_index = get_pokemon_index(fainted, player_pokemon_to_index)

                    game_state["player"]["seen_pokemon"][index]["mon"] = 'dead'
                    game_state["player"]["seen_pokemon"][index]["hp_percent"] = 0
                    player_remaining_mons -= 1
                    
                elif target.startswith("p2a"):
                    index, opponent_pokemon_to_index = get_pokemon_index(fainted, opponent_pokemon_to_index)
                    game_state["opponent"]["seen_pokemon"][index]["mon"] = 'dead'
                    game_state["opponent"]["seen_pokemon"][index]["hp_percent"] = 0
                    opponent_remaining -= 1

            elif event == "-boost":
                player = parts[2].split(' ')[0]
                if player.startswith("p1a"):
                    game_state['player']['boosts'][parts[3]] += (int(parts[4])/6)

                else:
                    game_state['opponent']['boosts'][parts[3]] += (int(parts[4])/6)
                
            elif event == "-unboost":
                player = parts[2].split(' ')[0]
                if player.startswith("p1a"):
                    game_state['player']['boosts'][parts[3]] -= (int(parts[4])/6)

                else:
                    game_state['opponent']['boosts'][parts[3]] -= (int(parts[4])/6)


            elif event == "-heal":
                info = parts[2].split(' ')
                player = info[0]
                pokemon = info[1]
                new_hp = parts[3].split('/')

                new_hp = round(int(new_hp[0])/int(new_hp[1].split(' ')[0]), 5)


                if player == 'p1a':

                    game_state['player']['active_pokemon']["hp_percent"] = new_hp
                    # player_seen[pokemon] = new_hp
                else:

                    game_state['opponent']['active_pokemon']["hp_percent"] = new_hp
                    # opponent_seen[pokemon] = new_hp
            elif event == '-status':
                info = parts[2].split(' ')
                player = info[0]
                pokemon = info[1]
                status = hot_one_status(parts[3])
                
                if player == 'p1a':
                    game_state['player']['active_pokemon']["status"] = status   
                else:
                    game_state['opponent']['active_pokemon']["status"] = status
            elif event == '-fieldstart':
                field = parts[2].split(' ')[1]
                if field == 'Trick':
                    game_state['battle_state']['trick_room'] = 1
                    game_state['battle_state']['trick_room_turns'] = 5
                else:
                    terrain = one_hot_encode_terrain(field)
                    game_state['battle_state']['weather'] = terrain   
                    game_state['battle_state']['weather_turns_left'] = 5   


            elif event == '-fieldend':

                terrain = parts[2].split(' ')[1]
                if terrain == "Trick":
                    game_state['battle_state']['trick_room'] = 0
                    game_state['battle_state']['trick_room_turns'] = 0
                else:
                    end = one_hot_encode_terrain('NoTerrain')
                    game_state['battle_state']['terrain'] = end
                    game_state['battle_state']['terrain_turns_left'] = 0
                pass

            elif event == '-weather':
                weather = parts[2]
                weather = one_hot_encode_weather(weather)
                game_state['battle_state']['weather'] = weather 
                print(parts)
                if weather[0] == 1:
                    game_state['battle_state']['weather_turns_left'] = 0

                elif len(parts) > 3 and parts[3] == '[upkeep]':
                    pass
                else:
                    game_state['battle_state']['weather_turns_left'] = 5  

            elif event =='-sidestart':
                side = parts[2]  # 'p1' or 'p2'
                
                if len(parts[3].split(' ')) > 1 : 
                    effect = parts[3].split(' ')[1]  
                else:
                    effect = parts[3]

                if side.startswith("p1a"):
                    if effect == "Reflect":
                        game_state['player']["player_side_effects"]['reflect_turns'] = 5
                    elif effect == "Tailwind":
                        game_state['player']["player_side_effects"]['tailwind_turns'] = 5
                    game_state['player']["player_side_effects"][effect] = 1
                else:
                    if effect == "Reflect":
                        game_state['opponent']["opponent_side_effects"]['reflect_turns'] = 5
                    elif effect == "Tailwind":
                        game_state['opponent']["opponent_side_effects"]['tailwind_turns'] = 5
                    game_state['opponent']["opponent_side_effects"][effect] = 1

            elif event =='-sideend':
                side = parts[2]  # 'p1' or 'p2'
                if len(parts[3].split(' ')) > 1 : 
                    effect = parts[3].split(' ')[1]  
                else:
                    effect = parts[3]

                if side.startswith("p1a"):
                    if effect == "Reflect":
                        game_state['player']["player_side_effects"]['reflect_turns'] = 0
                    elif effect == "Tailwind":
                        game_state['player']["player_side_effects"]['tailwind_turns'] = 0
                    game_state['player']["player_side_effects"][effect] = 0
                else:
                    if effect == "Reflect":
                        game_state['opponent']["opponent_side_effects"]['reflect_turns'] = 0
                    elif effect == "Tailwind":
                        game_state['opponent']["opponent_side_effects"]['tailwind_turns'] = 0
                    game_state['opponent']["opponent_side_effects"][effect] = 0
            elif event == '-terastallize':
                who = parts[1]
                tera = parts[2]
                if who.startswith('p1a'):
                    game_state['player']['active_pokemon']["terratype"] = hot_terratype('tera') 
                    game_state['player']['terra_used'] = 1
                elif who.startswith('p2a'):
                    game_state['opponent']['active_pokemon']["terratype"] = hot_terratype('tera') 
                    game_state['opponent']['terra_used'] = 1

                

                    

    return game_states

def replay_to_ml():

    all_game_states = []
    base_folder = 'all_un_parsed_replays'
    subfolders = ['12-11-replays', 'replays_json']

    for subfolder in subfolders:
        folder_path = os.path.join(base_folder, subfolder)
        for file in os.listdir(folder_path):
            filepath = os.path.join(folder_path, file)
            with open(filepath, 'r') as f:
                replay_data = json.load(f)
                log = replay_data['log']
                players = replay_data['players']
                p1 = players[0]
                opponent = players[1]
                opp_rating, winner, total_turns = get_opp_rating(log, opponent)
                if opp_rating:
                    opp_rating = int(opp_rating)
                    if opp_rating >= 1250:
                        p1_mons = extract_p1_pokemon(log)
                        game_states = parse_data(log, winner, opp_rating, p1, total_turns, 0.2, p1_mons)
                        # print(log)
                        all_game_states.extend(game_states)


   
    output_filepath = '12-11-game-states.json'
    with open(output_filepath, "w") as f:
        for state in all_game_states:
            json_line = json.dumps(state)  # Convert each game state to a compact JSON string
            f.write(json_line + "\n")  # Write each game state on its own line

    print(f'Game states exported to {output_filepath}')

replay_to_ml()

{'Terapagos': 'poke1', 'Lycanroc': 'poke2'}
{'Ursaluna': 'poke1'}
{'Terapagos': 'poke1', 'Lycanroc': 'poke2'}
{'Ursaluna': 'poke1'}
{'Ursaluna': 'poke1', 'Luvdisc': 'poke2'}
{'Copperajah': 'poke1', 'Mesprit': 'poke2', 'Ludicolo': 'poke3', 'Dondozo': 'poke4', 'Mudsdale': 'poke5', 'Pikachu': 'poke6'}
{'Sawsbuck': 'poke1'}
{'Sawsbuck': 'poke1'}
{'Sawsbuck': 'poke1', 'Delphox': 'poke2'}
{'Sawsbuck': 'poke1', 'Delphox': 'poke2', 'Camerupt': 'poke3'}
{'Copperajah': 'poke1', 'Mesprit': 'poke2', 'Ludicolo': 'poke3', 'Dondozo': 'poke4', 'Mudsdale': 'poke5', 'Pikachu': 'poke6'}
{'Sawsbuck': 'poke1', 'Delphox': 'poke2', 'Camerupt': 'poke3', 'Enamorus': 'poke4'}
{'Copperajah': 'poke1', 'Mesprit': 'poke2', 'Ludicolo': 'poke3', 'Dondozo': 'poke4', 'Mudsdale': 'poke5', 'Pikachu': 'poke6'}
{'Copperajah': 'poke1', 'Mesprit': 'poke2', 'Ludicolo': 'poke3', 'Dondozo': 'poke4', 'Mudsdale': 'poke5', 'Pikachu': 'poke6'}
{'Sawsbuck': 'poke1', 'Delphox': 'poke2', 'Camerupt': 'poke3', 'Enamorus': 'poke4', 'Gogo

gonna do 2 different modelks one for wr one for moves